In [1]:
from fastai import *
from fastai.vision import *
import tqdm

PATH = Path('../..').resolve()

seed = 12345

%matplotlib inline

In [2]:
sys.path.append(f'{PATH}/src')

from mxresnet import *
from ranger import Ranger



Mish activation loaded...
Mish activation loaded...


In [3]:
xGASS_stats = [tensor([-0.0169, -0.0105, -0.0004]), tensor([0.9912, 0.9968, 1.0224])]

tfms = get_transforms(
    do_flip=True,
    flip_vert=True,
    max_zoom=1.0,
    max_rotate=15.0,
    max_lighting=0,
    max_warp=0,
)

# Try using ALFALFA only

In [4]:
df = pd.read_csv(f"{PATH}/data/a40-SDSS_gas-frac.csv")

In [5]:
src = (
    ImageList.from_df(
        df, path=PATH, folder="images-legacy", suffix=".jpg", cols="AGCNr"
    )
    .split_by_rand_pct(0.2, seed=seed)
    .label_from_df(cols=["logfgas"], label_cls=FloatList)
)

data = (
    src.transform(tfms, size=224)
    .databunch(bs=32)
    .normalize(xGASS_stats)
)

In [6]:
model = mxresnet50()
model[-1] = nn.Linear(model[-1].in_features, 1, bias=True)

In [7]:
learn = Learner(
    data,
    model=model,
    opt_func=partial(Ranger),
    loss_func=root_mean_squared_error,
    wd=1e-3,
    bn_wd=False,
    true_wd=True,
)

In [8]:
learn.load('best_a40A-50');

set state called


# Load data set

## Note: some of these images are outside the SDSS footprint, so let's remove them on the basis of the images that are already downloaded.

In [86]:
nibles = pd.read_csv(f'{PATH}/data/NIBLES_clean.csv')

In [87]:
nibles = nibles[(nibles.logMstar > 8) & np.isfinite(nibles.logfgas)].copy()

In [88]:
nible_ids = np.array([p.stem for p in list(PATH.glob(pattern='images-nibles/*.jpg'))], dtype=int)

In [89]:
nibles.set_index('nibles_id', inplace=True)
nibles.drop([obj for obj in nibles.index if obj not in nible_ids], inplace=True)
nibles.reset_index(inplace=True)

## insert as validation and predict

In [90]:
nibles_data = (
    ImageList.from_df(nibles, path=PATH, folder="images-nibles", suffix=".jpg", cols="nibles_id")
        .split_none()
        .label_from_df(cols=["logfgas"], label_cls=FloatList)
    .transform(tfms, size=224)
    .databunch(bs=128)
    .normalize(xGASS_stats)
)

In [91]:
learn.data.valid_dl = nibles_data.train_dl

In [92]:
learn.validate()

[0.6861801]

In [93]:
learn.show_results()

Okay, quite a number of these don't even have optical counterparts (or are improperly centered)!

# Even more cleaned test sample

I went through and removed the following:
- images with no apparent optical source in the center (since those were likely to have faulty stellar mass estimates)
- images with only a point source in the center (only one or two, again these are likely mismatches)
- images corrupted by bleed from stars or flatfielding issues (only two)

Note that these do *not* include very low surface brightness galaxies; so long as they are detectable in imaging, I left them in.

Remaining: 942 / 1585 (59%)

In [15]:
nibles = pd.read_csv(f'{PATH}/data/NIBLES_clean.csv')
nibles = nibles[(nibles.logMstar > 8) & np.isfinite(nibles.logfgas)].copy()

In [12]:
nible_ids = np.array([p.stem for p in list(PATH.glob(pattern='images-nibles_cleaned/*.jpg'))], dtype=int)

In [16]:
nibles.set_index('nibles_id', inplace=True)
nibles.drop([obj for obj in nibles.index if obj not in nible_ids], inplace=True)
nibles.reset_index(inplace=True)

In [17]:
nibles_data = (
    ImageList.from_df(nibles, path=PATH, folder="images-nibles", suffix=".jpg", cols="nibles_id")
        .split_none()
        .label_from_df(cols=["logfgas"], label_cls=FloatList)
    .transform(tfms, size=224)
    .databunch(bs=128)
    .normalize(xGASS_stats)
)

In [18]:
learn.data.valid_dl = nibles_data.train_dl

In [108]:
results = np.zeros((len(learn.data.valid_ds), 2))

for i, [x,y] in tqdm.tqdm(enumerate(learn.data.valid_ds), total=len(results)):
    p = learn.predict(x)[0]
    results[i] = [float(p.data[0]), float(y.data)]

100%|██████████| 942/942 [06:28<00:00,  2.42it/s]


In [110]:
results.shape

(942, 2)

In [118]:
((results[:,0] - results[:,1])**2).mean()**0.5

0.37396779151127446

In [119]:
plt.figure(figsize=(6, 6))


plt.scatter(results[:,1], results[:,0], c='k', s=5)

plt.plot([-3, 3], [-3, 3])
plt.gca().set_aspect('equal')
plt.xlim(-3, 2)
plt.ylim(-3, 2)

(-3, 2)

In [120]:
res_df = pd.DataFrame({'nibles_id': nibles.nibles_id, 'fgas_true': results[:,1], 'fgas_pred': results[:,0]})

In [121]:
res_df.to_csv(f'{PATH}/results/nibles/nibles_clean_results.csv', index=False)

## Compare results to quoted 45% overprediction between NIBLES & ALFALFA


In [167]:
recalibration = np.log10(1.45) # dex units

In [168]:
np.median(res_df.fgas_pred - res_df.fgas_true), recalibration

(0.13406360149383545, 0.16136800223497488)

In [169]:
((res_df.fgas_pred - (res_df.fgas_true + recalibration))**2).mean()**0.5

0.3458833684900825

In [179]:
res_df.sample(3)

nibles_id  fgas_true  fgas_pred
128        534       0.22   0.473260
672       1974      -0.86  -0.468255
701       2046      -0.27  -0.244856

## Examine most overpredicted

In [180]:
def load_image(idx, df, ax=None, annotate=True):
    """Helper function to load and annotate image"""
    
    if not ax:
        fig, ax = plt.subplots(1, 1, figsize=(4, 4))
        
    fgas_true, fgas_pred = df.iloc[idx]
    name = df.index[idx]
    
    # get image
    image = plt.imread(f'{PATH}/images-nibles_cleaned/{name}.jpg')
    ax.imshow(image)
    ax.axis('off')
    
    # label
    if annotate:
        fontdict = dict(color='white', size=18)
        ax.text(0.5, 0.9, f'NIBLES #{name}', fontdict=fontdict, transform=ax.transAxes, ha='center', va='bottom')
        ax.text(0.95, 0.125, r'$\mathcal{M}_{\rm true}$' + f' = {fgas_true: .3f}', fontdict=fontdict, transform=ax.transAxes, ha='right', va='bottom')
        ax.text(0.95, 0.025, r'$\mathcal{M}_{\rm pred}$' + f' = {fgas_pred: .3f}', fontdict=fontdict, transform=ax.transAxes, ha='right', va='bottom')

In [181]:
overestimated = res_df.iloc[np.argsort(res_df.fgas_true - res_df.fgas_pred)]
overestimated.set_index('nibles_id', inplace=True)

In [182]:
fig, axes = plt.subplots(4, 5, figsize=(20, 16))
for idx in range(20):
    ax = axes.flat[idx]
    load_image(idx, overestimated, ax=ax)
    
fig.tight_layout()
fig.subplots_adjust(wspace=0.02, hspace=0.02, left=0.02)
fig.text(0, 0.5, r'Most overestimated in NIBLES', rotation=90, fontsize=24, va='center');

Some of these are probably not legit, e.g., 2044 is clearly a blank field, and I went venture that most of the blue spirals in here are actually better estimated than in NIBLES.

## Most underpredicted

In [183]:
underestimated = res_df.iloc[np.argsort(res_df.fgas_pred - res_df.fgas_true )]
underestimated.set_index('nibles_id', inplace=True)

In [184]:
fig, axes = plt.subplots(4, 5, figsize=(20, 16))
for idx in range(20):
    ax = axes.flat[idx]
    load_image(idx, underestimated, ax=ax)
    
fig.tight_layout()
fig.subplots_adjust(wspace=0.02, hspace=0.02, left=0.02)
fig.text(0, 0.5, r'Most underestimate in NIBLES', rotation=90, fontsize=24, va='center');

Honestly, some of these feel suspicious to me too. Perhaps the dust is obscuring seriously gas-rich, star-forming regions... But in many of these, our CNN is underestimating HI mass because the galaxy is larger than the field of view.

# Repeat with combined xGASS + ALFALFA learner